In [1]:
import os
import sys
import math
import operator
import numpy as np
import pandas as pd
import pickle as pkl
import tifffile as tif
from keras.utils.np_utils import to_categorical
from keras.layers import Dense
from keras.layers import Conv2D
from multiprocessing import Pool
from keras.utils import Sequence
from keras.layers import Flatten
from keras.layers import MaxPool2D
from keras.models import Sequential 
from keras.layers import Reshape
from collections import OrderedDict
from keras.layers import TimeDistributed
from keras.layers import LSTM
from keras.layers import Permute
from keras.models import load_model, save_model
os.chdir("../../")

Using TensorFlow backend.


In [23]:
class RNN_train:
    
    def __init__(self, directory, time_steps):
        
        self.path = directory
        self.time_steps = time_steps
        
        with open("Data/hierarchy_data.pkl","rb") as f:
            hd = pkl.load(f)
        with open("Data/class_encoding.pkl","rb") as f:
            self.classes = pkl.load(f)
        with open("Data/order_encoding.pkl","rb") as f:
            self.orders = pkl.load(f)
        with open("Data/family_encoding.pkl","rb") as f:
            self.families = pkl.load(f)
        with open("Data/genus_encoding.pkl","rb") as f:
            self.genuses = pkl.load(f)
        with open("Data/specie_encoding.pkl","rb") as f:
            self.species = pkl.load(f)
            
        self.train_seq = []
        self.test_seq = []
                
        for cls in hd.keys():
            for order in hd[cls].keys():
                for family in hd[cls][order].keys():
                    for genus in hd[cls][order][family].keys():
                        for specie in hd[cls][order][family][genus]:
                            for im in os.listdir(self.path+"train/"+str(self.classes[cls])+"/"+str(self.orders[order])
                                                 +"/"+str(self.families[family])+"/"+str(self.genuses[genus])+"/"+str(specie)):
                                self.train_seq.append(([self.classes[cls],0,0,0],
                                                      [self.orders[order],self.families[family],
                                                       self.genuses[genus],specie]))
                            for im in os.listdir(self.path+"test/"+str(self.classes[cls])+"/"+str(self.orders[order])
                                                 +"/"+str(self.families[family])+"/"+str(self.genuses[genus])+"/"+str(specie)):
                                self.test_seq.append(([self.classes[cls],0,0,0],
                                                      [self.orders[order],self.families[family],
                                                       self.genuses[genus],specie]))
        
        np.random.shuffle(self.train_seq)
        np.random.shuffle(self.test_seq)
        
        self.xtrain = np.array([t[0] for t in self.train_seq])
        self.ytrain = np.array([t[1] for t in self.train_seq])
        self.xtest = np.array([t[0] for t in self.test_seq])
        self.ytest = np.array([t[1] for t in self.test_seq])
        
        self.xtrain = np.reshape(self.xtrain,(self.xtrain.shape[0],self.xtrain.shape[1],1))
        self.ytrain = np.reshape(self.ytrain,(self.ytrain.shape[0],self.ytrain.shape[1],1))
        self.xtest = np.reshape(self.xtest,(self.xtest.shape[0],self.xtest.shape[1],1))
        self.ytest = np.reshape(self.ytest,(self.ytest.shape[0],self.ytest.shape[1],1))
        
        print(self.xtrain.shape, self.ytrain.shape, self.xtest.shape, self.ytest.shape)
        
    def RNN_Model(self):
        
        model = Sequential()
        model.add(LSTM(300, return_sequences=True, input_shape=(self.xtrain.shape[1],1)))
        model.add(LSTM(200, return_sequences=True))
        model.add(LSTM(100, return_sequences=True))
        model.add(Dense(512, activation='relu'))
        model.add(Dense(256, activation='relu'))
        model.add(Dense(128, activation='relu'))
        model.add(Dense(1))
        model.summary()
        
        model.compile(loss='logcosh', optimizer='Nadam', metrics=['mae'])
        model.fit(self.xtrain, self.ytrain, batch_size=100, epochs=10)
        scores = model.evaluate(self.xtest, self.ytest)
        return model, scores

In [24]:
ob = RNN_train("Data/Hierarchial Data/", 4)

(152980, 4, 1) (152980, 4, 1) (65563, 4, 1) (65563, 4, 1)


In [25]:
model, scores = ob.RNN_Model()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_7 (LSTM)                (None, 4, 300)            362400    
_________________________________________________________________
lstm_8 (LSTM)                (None, 4, 200)            400800    
_________________________________________________________________
lstm_9 (LSTM)                (None, 4, 100)            120400    
_________________________________________________________________
dense_25 (Dense)             (None, 4, 512)            51712     
_________________________________________________________________
dense_26 (Dense)             (None, 4, 256)            131328    
_________________________________________________________________
dense_27 (Dense)             (None, 4, 128)            32896     
_________________________________________________________________
dense_28 (Dense)             (None, 4, 1)              129       
Total para

In [26]:
scores

[217.92864908614294, 218.58824205076368]

In [27]:
y_pred = model.predict(ob.xtest, batch_size=30)

In [28]:
for i in range(len(y_pred)):
    for j in range(4):
        print(y_pred[i][j], ob.ytest[i][j])
    print("\n")

[22.400644] [25]
[63.43724] [133]
[592.95526] [402]
[771.41797] [488]


[22.400644] [29]
[63.43724] [81]
[592.95526] [765]
[771.41797] [799]


[22.400644] [1]
[63.43724] [9]
[592.95526] [863]
[771.41797] [3294]


[22.400644] [22]
[63.43724] [63]
[592.95526] [852]
[771.41797] [1139]


[22.400644] [23]
[63.43724] [64]
[592.95526] [193]
[771.41797] [314]


[40.499977] [43]
[106.974655] [119]
[471.93307] [712]
[745.76105] [3204]


[22.400644] [5]
[63.43724] [19]
[592.95526] [728]
[771.41797] [98]


[22.400644] [5]
[63.43724] [19]
[592.95526] [857]
[771.41797] [890]


[22.400644] [29]
[63.43724] [116]
[592.95526] [214]
[771.41797] [340]


[40.499977] [43]
[106.974655] [119]
[471.93307] [460]
[745.76105] [548]


[22.400644] [36]
[63.43724] [103]
[592.95526] [650]
[771.41797] [70]


[22.400644] [9]
[63.43724] [6]
[592.95526] [223]
[771.41797] [343]


[22.400644] [5]
[63.43724] [19]
[592.95526] [478]
[771.41797] [557]


[40.499977] [43]
[106.974655] [119]
[471.93307] [439]
[745.76105] [1996]



[22.400644] [22]
[63.43724] [63]
[592.95526] [307]
[771.41797] [2875]


[22.400644] [40]
[63.43724] [108]
[592.95526] [673]
[771.41797] [734]


[22.400644] [35]
[63.43724] [90]
[592.95526] [583]
[771.41797] [26]


[22.400644] [47]
[63.43724] [132]
[592.95526] [34]
[771.41797] [195]


[22.400644] [47]
[63.43724] [132]
[592.95526] [275]
[771.41797] [2283]


[22.400644] [34]
[63.43724] [135]
[592.95526] [821]
[771.41797] [853]


[22.400644] [6]
[63.43724] [26]
[592.95526] [779]
[771.41797] [807]


[22.400644] [22]
[63.43724] [63]
[592.95526] [528]
[771.41797] [3036]


[22.400644] [18]
[63.43724] [54]
[592.95526] [879]
[771.41797] [866]


[22.400644] [5]
[63.43724] [19]
[592.95526] [7]
[771.41797] [176]


[22.400644] [35]
[63.43724] [90]
[592.95526] [583]
[771.41797] [26]


[22.400644] [5]
[63.43724] [19]
[592.95526] [478]
[771.41797] [556]


[22.400644] [22]
[63.43724] [63]
[592.95526] [528]
[771.41797] [599]


[40.499977] [31]
[106.974655] [144]
[471.93307] [880]
[745.76105] [1158]


[44

[771.41797] [1800]


[22.400644] [34]
[63.43724] [75]
[592.95526] [477]
[771.41797] [555]


[40.499977] [4]
[106.974655] [17]
[471.93307] [665]
[745.76105] [124]


[22.400644] [1]
[63.43724] [9]
[592.95526] [256]
[771.41797] [360]


[22.400644] [34]
[63.43724] [62]
[592.95526] [597]
[771.41797] [669]


[22.400644] [40]
[63.43724] [108]
[592.95526] [673]
[771.41797] [54]


[22.400644] [22]
[63.43724] [63]
[592.95526] [139]
[771.41797] [85]


[40.499977] [43]
[106.974655] [119]
[471.93307] [28]
[745.76105] [185]


[22.400644] [5]
[63.43724] [19]
[592.95526] [236]
[771.41797] [350]


[22.400644] [51]
[63.43724] [44]
[592.95526] [853]
[771.41797] [884]


[22.400644] [22]
[63.43724] [63]
[592.95526] [947]
[771.41797] [954]


[22.400644] [5]
[63.43724] [19]
[592.95526] [361]
[771.41797] [1786]


[22.400644] [46]
[63.43724] [129]
[592.95526] [445]
[771.41797] [1548]


[22.400644] [47]
[63.43724] [155]
[592.95526] [688]
[771.41797] [16]


[22.400644] [22]
[63.43724] [63]
[592.95526] [947]
[771

[63.43724] [19]
[592.95526] [442]
[771.41797] [762]


[22.400644] [1]
[63.43724] [13]
[592.95526] [433]
[771.41797] [84]


[22.400644] [5]
[63.43724] [19]
[592.95526] [438]
[771.41797] [532]


[22.400644] [47]
[63.43724] [154]
[592.95526] [968]
[771.41797] [978]


[40.499977] [43]
[106.974655] [119]
[471.93307] [439]
[745.76105] [1996]


[22.400644] [29]
[63.43724] [81]
[592.95526] [31]
[771.41797] [46]


[44.30442] [39]
[20.05217] [107]
[107.42145] [670]
[790.44556] [731]


[22.400644] [9]
[63.43724] [35]
[592.95526] [900]
[771.41797] [921]


[22.400644] [1]
[63.43724] [13]
[592.95526] [433]
[771.41797] [84]


[22.400644] [22]
[63.43724] [63]
[592.95526] [852]
[771.41797] [1139]


[22.400644] [9]
[63.43724] [35]
[592.95526] [818]
[771.41797] [850]


[22.400644] [23]
[63.43724] [78]
[592.95526] [498]
[771.41797] [2325]


[22.400644] [5]
[63.43724] [19]
[592.95526] [857]
[771.41797] [889]


[22.400644] [1]
[63.43724] [9]
[592.95526] [377]
[771.41797] [1461]


[40.499977] [31]
[106.97465

[63.43724] [19]
[592.95526] [280]
[771.41797] [382]


[22.400644] [35]
[63.43724] [38]
[592.95526] [436]
[771.41797] [1863]


[22.400644] [29]
[63.43724] [81]
[592.95526] [765]
[771.41797] [799]


[22.400644] [34]
[63.43724] [62]
[592.95526] [372]
[771.41797] [1800]


[22.400644] [22]
[63.43724] [63]
[592.95526] [890]
[771.41797] [76]


[22.400644] [22]
[63.43724] [63]
[592.95526] [406]
[771.41797] [497]


[22.400644] [23]
[63.43724] [64]
[592.95526] [786]
[771.41797] [60]


[22.400644] [7]
[63.43724] [27]
[592.95526] [185]
[771.41797] [293]


[22.400644] [29]
[63.43724] [116]
[592.95526] [738]
[771.41797] [772]


[22.400644] [29]
[63.43724] [81]
[592.95526] [517]
[771.41797] [587]


[22.400644] [7]
[63.43724] [130]
[592.95526] [793]
[771.41797] [830]


[22.400644] [29]
[63.43724] [81]
[592.95526] [244]
[771.41797] [1537]


[22.400644] [5]
[63.43724] [19]
[592.95526] [286]
[771.41797] [391]


[40.499977] [43]
[106.974655] [119]
[471.93307] [606]
[745.76105] [674]


[22.400644] [29]
[63

...

[592.95526] [566]
[771.41797] [3235]


[40.499977] [43]
[106.974655] [119]
[471.93307] [299]
[745.76105] [395]


[22.400644] [7]
[63.43724] [130]
[592.95526] [793]
[771.41797] [144]


[22.400644] [29]
[63.43724] [81]
[592.95526] [595]
[771.41797] [666]


[22.400644] [34]
[63.43724] [62]
[592.95526] [372]
[771.41797] [1800]


[22.400644] [7]
[63.43724] [27]
[592.95526] [539]
[771.41797] [154]


[22.400644] [5]
[63.43724] [19]
[592.95526] [127]
[771.41797] [48]


[22.400644] [22]
[63.43724] [63]
[592.95526] [406]
[771.41797] [1842]


[40.499977] [4]
[106.974655] [105]
[471.93307] [658]
[745.76105] [2673]


[22.400644] [9]
[63.43724] [118]
[592.95526] [552]
[771.41797] [3072]


[22.400644] [47]
[63.43724] [132]
[592.95526] [411]
[771.41797] [100]


[22.400644] [29]
[63.43724] [81]
[592.95526] [765]
[771.41797] [799]


[40.499977] [4]
[106.974655] [7]
[471.93307] [38]
[745.76105] [1351]


[22.400644] [22]
[63.43724] [63]
[592.95526] [947]
[771.41797] [954]


[22.400644] [5]
[63.43724] [19]

[22.400644] [47]
[63.43724] [96]
[592.95526] [383]
[771.41797] [102]


[22.400644] [22]
[63.43724] [63]
[592.95526] [588]
[771.41797] [658]


[40.499977] [4]
[106.974655] [105]
[471.93307] [660]
[745.76105] [9]


[22.400644] [47]
[63.43724] [132]
[592.95526] [814]
[771.41797] [2537]


[22.400644] [51]
[63.43724] [44]
[592.95526] [707]
[771.41797] [1136]


[40.499977] [43]
[106.974655] [153]
[471.93307] [965]
[745.76105] [974]


[40.499977] [4]
[106.974655] [105]
[471.93307] [660]
[745.76105] [43]


[22.400644] [46]
[63.43724] [129]
[592.95526] [789]
[771.41797] [819]


[22.400644] [22]
[63.43724] [63]
[592.95526] [984]
[771.41797] [1018]


[22.400644] [29]
[63.43724] [102]
[592.95526] [391]
[771.41797] [479]


[22.400644] [47]
[63.43724] [132]
[592.95526] [761]
[771.41797] [2680]


[22.400644] [34]
[63.43724] [62]
[592.95526] [372]
[771.41797] [462]


[22.400644] [22]
[63.43724] [63]
[592.95526] [984]
[771.41797] [1250]


[22.400644] [7]
[63.43724] [27]
[592.95526] [185]
[771.41797] [2

[745.76105] [395]


[40.499977] [43]
[106.974655] [119]
[471.93307] [743]
[745.76105] [779]


[22.400644] [5]
[63.43724] [19]
[592.95526] [857]
[771.41797] [890]


[22.400644] [23]
[63.43724] [64]
[592.95526] [193]
[771.41797] [314]


[44.30442] [44]
[20.05217] [123]
[107.42145] [752]
[790.44556] [1044]


[40.499977] [43]
[106.974655] [79]
[471.93307] [499]
[745.76105] [1583]


[22.400644] [22]
[63.43724] [63]
[592.95526] [947]
[771.41797] [954]


[22.400644] [47]
[63.43724] [132]
[592.95526] [887]
[771.41797] [2085]


[22.400644] [5]
[63.43724] [19]
[592.95526] [886]
[771.41797] [119]


[40.499977] [4]
[106.974655] [7]
[471.93307] [397]
[745.76105] [1829]


[22.400644] [6]
[63.43724] [26]
[592.95526] [621]
[771.41797] [687]


[22.400644] [21]
[63.43724] [127]
[592.95526] [763]
[771.41797] [797]


[22.400644] [1]
[63.43724] [9]
[592.95526] [731]
[771.41797] [1714]


[22.400644] [29]
[63.43724] [116]
[592.95526] [738]
[771.41797] [3216]


[22.400644] [9]
[63.43724] [6]
[592.95526] [44]


[63.43724] [133]
[592.95526] [402]
[771.41797] [488]


[22.400644] [22]
[63.43724] [63]
[592.95526] [806]
[771.41797] [841]


[22.400644] [40]
[63.43724] [108]
[592.95526] [673]
[771.41797] [734]


[22.400644] [23]
[63.43724] [64]
[592.95526] [786]
[771.41797] [1075]


[22.400644] [5]
[63.43724] [19]
[592.95526] [941]
[771.41797] [947]


[41.162712] [41]
[114.090324] [114]
[589.0102] [733]
[804.4396] [766]


[22.400644] [25]
[63.43724] [133]
[592.95526] [402]
[771.41797] [488]


[22.400644] [9]
[63.43724] [122]
[592.95526] [751]
[771.41797] [788]


[40.499977] [43]
[106.974655] [119]
[471.93307] [455]
[745.76105] [547]


[22.400644] [22]
[63.43724] [63]
[592.95526] [806]
[771.41797] [841]


[40.499977] [43]
[106.974655] [119]
[471.93307] [154]
[745.76105] [274]


[22.400644] [47]
[63.43724] [155]
[592.95526] [688]
[771.41797] [16]


[22.400644] [25]
[63.43724] [133]
[592.95526] [402]
[771.41797] [488]


[22.400644] [7]
[63.43724] [27]
[592.95526] [185]
[771.41797] [295]


[22.400644] [

KeyboardInterrupt: 